to do: cut out the extremely long plays so padding is more reasonable 

context tensor is fine, play-by-play tensor may need to work on the features, model used: lstm 

ADD THE INDICATOR FOR SPECIFIC PLAYER MOTIONS TO PLAYER TENSOR

FIX THE ENCODING FOR QUARTERS & DOWNS 

remove the 'Other' plays that are labelled 

# install and import

In [220]:
!pip install skrub

     |████████████████████████████████| 327 kB 11.1 MB/s eta 0:00:01
You should consider upgrading via the '/Users/victorhau/.pyenv/versions/3.10.2/bin/python3.10 -m pip install --upgrade pip' command.


In [223]:
import skrub as kr
import polars as pl
import numpy as np
import torch

In [496]:
presnap = pl.read_csv("data/outputs/presnap.csv")

In [5]:
processed = pl.read_csv("data/outputs/processed.csv")

In [497]:
list(presnap['pff_passCoverage'].unique()) # return the unique defensive pass coverages 

presnap = presnap.with_columns(
    pl.when(pl.col("pff_passCoverage") == "Cover-1 Double").then(pl.lit("Cover-1"))
    .when(pl.col("pff_passCoverage") == "Cover-3 Cloud Left").then(pl.lit("Cover-3"))
    .when(pl.col("pff_passCoverage") == "Cover-3 Cloud Right").then(pl.lit("Cover-3"))
    .when(pl.col("pff_passCoverage") == "Cover-3 Double Cloud").then(pl.lit("Cover-3"))
    .when(pl.col("pff_passCoverage") == "Cover-3 Seam").then(pl.lit("Cover-3"))
    .when(pl.col("pff_passCoverage") == "Cover 6-Left").then(pl.lit("Cover-6"))
    .when(pl.col("pff_passCoverage") == "Cover-6 Right").then(pl.lit("Cover-6"))
    .when(pl.col("pff_passCoverage") == "Miscellaneous").then(pl.lit("Other"))
    .when(pl.col("pff_passCoverage") == "None").then(pl.lit("Other"))
    .otherwise(pl.col("pff_passCoverage"))
    .alias("pff_passCoverage")
) # set the pff_passCoverage row values to one of 4 covers 

presnap = presnap.filter(
    (~pl.col("pff_passCoverage").is_in(["Prevent", "Bracket"]))
) # exclude prevents and bracket 
presnap.filter(pl.col('pff_manZone') == 'Zone')

shape: (3_348_488, 127)
┌────────────┬────────┬───────┬───────────────┬───┬────────┬────────────┬───────────────┬──────────┐
│ gameId     ┆ playId ┆ nflId ┆ displayName   ┆ … ┆ weight ┆ birthDate  ┆ collegeName   ┆ position │
│ ---        ┆ ---    ┆ ---   ┆ ---           ┆   ┆ ---    ┆ ---        ┆ ---           ┆ ---      │
│ i64        ┆ i64    ┆ i64   ┆ str           ┆   ┆ i64    ┆ str        ┆ str           ┆ str      │
╞════════════╪════════╪═══════╪═══════════════╪═══╪════════╪════════════╪═══════════════╪══════════╡
│ 2022090800 ┆ 1      ┆ 35472 ┆ Rodger        ┆ … ┆ 325    ┆ 1988-06-06 ┆ Indiana       ┆ G        │
│            ┆        ┆       ┆ Saffold       ┆   ┆        ┆            ┆               ┆          │
│ 2022090800 ┆ 1      ┆ 42392 ┆ Mitch Morse   ┆ … ┆ 305    ┆ 1992-04-21 ┆ Missouri      ┆ C        │
│ 2022090800 ┆ 1      ┆ 42489 ┆ Stefon Diggs  ┆ … ┆ 191    ┆ 1993-11-29 ┆ Maryland      ┆ WR       │
│ 2022090800 ┆ 1      ┆ 44875 ┆ Dion Dawkins  ┆ … ┆ 320    ┆ 1994-04-26 ┆ Temple        ┆ T        │
│ 2022090800 ┆ 1      ┆ 44985 ┆ Isaiah        ┆ … ┆ 173    ┆ 1995-04-09 ┆ Georgia       ┆ WR       │
│            ┆        ┆       ┆ McKenzie      ┆   ┆        ┆            ┆               ┆          │
│ …          ┆ …      ┆ …     ┆ …             ┆ … ┆ …      ┆ …          ┆ …             ┆ …        │
│ 2022091901 ┆ 108    ┆ 47974 ┆ Marcus Epps   ┆ … ┆ 191    ┆ 1996-01-27 ┆ Wyoming       ┆ SS       │
│ 2022091901 ┆ 108    ┆ 48516 ┆ T.J. Edwards  ┆ … ┆ 240    ┆ 1996-08-12 ┆ Wisconsin     ┆ ILB      │
│ 2022091901 ┆ 108    ┆ 52545 ┆ Josiah Scott  ┆ … ┆ 175    ┆ 1999-04-05 ┆ Michigan      ┆ CB       │
│            ┆        ┆       ┆               ┆   ┆        ┆            ┆ State         ┆          │
│ 2022091901 ┆ 108    ┆ 53552 ┆ Zech          ┆ … ┆ 195    ┆ NA         ┆ Texas Tech    ┆ CB       │
│            ┆        ┆       ┆ McPhearson    ┆   ┆        ┆            ┆               ┆          │
│ 2022091901 ┆ 108    ┆ 53663 ┆ Patrick       ┆ … ┆ 251    ┆ NA         ┆ Tulane        ┆ OLB      │
│            ┆        ┆       ┆ Johnson       ┆   ┆        ┆            ┆               ┆          │
└────────────┴────────┴───────┴───────────────┴───┴────────┴────────────┴───────────────┴──────────┘

creating extra features

In [498]:
presnap = presnap.with_columns(
    (pl.col("defensiveTeam") == pl.col("club")).alias("def")
)

# label

In [518]:
col_for_label = ['Id', 'frameId', 'pff_manZone', 'pff_passCoverage']
label_table = presnap.select(col_for_label).unique(maintain_order=True)


shape: (212_214, 4)
┌────────────────┬─────────┬─────────────┬──────────────────┐
│ Id             ┆ frameId ┆ pff_manZone ┆ pff_passCoverage │
│ ---            ┆ ---     ┆ ---         ┆ ---              │
│ str            ┆ i64     ┆ str         ┆ str              │
╞════════════════╪═════════╪═════════════╪══════════════════╡
│ 2022090800_1   ┆ 76      ┆ Zone        ┆ Cover-6          │
│ 2022090800_1   ┆ 77      ┆ Zone        ┆ Cover-6          │
│ 2022090800_1   ┆ 78      ┆ Zone        ┆ Cover-6          │
│ 2022090800_1   ┆ 79      ┆ Zone        ┆ Cover-6          │
│ 2022090800_1   ┆ 80      ┆ Zone        ┆ Cover-6          │
│ …              ┆ …       ┆ …           ┆ …                │
│ 2022091901_111 ┆ 75      ┆ Other       ┆ Red Zone         │
│ 2022091901_111 ┆ 76      ┆ Other       ┆ Red Zone         │
│ 2022091901_111 ┆ 77      ┆ Other       ┆ Red Zone         │
│ 2022091901_111 ┆ 78      ┆ Other       ┆ Red Zone         │
│ 2022091901_111 ┆ 79      ┆ Other       ┆ Red Zone         │
└────────────────┴─────────┴─────────────┴──────────────────┘

In [627]:
other_plays = label_table.filter(pl.col("pff_manZone") == 'Other').select(pl.col('Id')).unique().to_series().to_list()
presnap = presnap.filter(~pl.col('Id').is_in(other_plays))

label_table = label_table.filter(~pl.col('Id').is_in(other_plays))

# context tensor

### number of position on field

In [559]:
presnap.filter(pl.col("position").is_null()).unique(pl.col('displayName')) #some players positions are null
player_pos_map = {"Robby Anderson": "WR", "Cameron Sample":'DE', 'Zachary Carter':'DT', 'Daxton Hill':'CB', 'Jacob Martin':'DE', 'Joe Fortson':'TE', 'Josh Allen':'DE', 'Decobie Durant':'CB'}
presnap = presnap.with_columns(pl.col('position').fill_null(pl.col("displayName").replace(player_pos_map)))

In [560]:
# calculate the number of position on the field 
# all positions
all_pos = presnap.select("position").unique().to_series().to_list()
#create a pivot table for the position column on each play do not ask man
number_of_players_per_pos = presnap.pivot(values="position",
              index = ["Id", 'frameId'],
              on="position",
              aggregate_function="len").fill_null(0)
number_of_players_per_pos

shape: (203_408, 21)
┌────────────────┬─────────┬─────┬─────┬───┬─────┬─────┬─────┬─────┐
│ Id             ┆ frameId ┆ G   ┆ C   ┆ … ┆ OLB ┆ MLB ┆ DB  ┆ LB  │
│ ---            ┆ ---     ┆ --- ┆ --- ┆   ┆ --- ┆ --- ┆ --- ┆ --- │
│ str            ┆ i64     ┆ u32 ┆ u32 ┆   ┆ u32 ┆ u32 ┆ u32 ┆ u32 │
╞════════════════╪═════════╪═════╪═════╪═══╪═════╪═════╪═════╪═════╡
│ 2022090800_1   ┆ 76      ┆ 1   ┆ 2   ┆ … ┆ 0   ┆ 0   ┆ 0   ┆ 0   │
│ 2022090800_1   ┆ 77      ┆ 1   ┆ 2   ┆ … ┆ 0   ┆ 0   ┆ 0   ┆ 0   │
│ 2022090800_1   ┆ 78      ┆ 1   ┆ 2   ┆ … ┆ 0   ┆ 0   ┆ 0   ┆ 0   │
│ 2022090800_1   ┆ 79      ┆ 1   ┆ 2   ┆ … ┆ 0   ┆ 0   ┆ 0   ┆ 0   │
│ 2022090800_1   ┆ 80      ┆ 1   ┆ 2   ┆ … ┆ 0   ┆ 0   ┆ 0   ┆ 0   │
│ …              ┆ …       ┆ …   ┆ …   ┆ … ┆ …   ┆ …   ┆ …   ┆ …   │
│ 2022091901_107 ┆ 16      ┆ 2   ┆ 1   ┆ … ┆ 1   ┆ 0   ┆ 0   ┆ 0   │
│ 2022091901_108 ┆ 1       ┆ 2   ┆ 1   ┆ … ┆ 1   ┆ 0   ┆ 0   ┆ 0   │
│ 2022091901_108 ┆ 2       ┆ 2   ┆ 1   ┆ … ┆ 1   ┆ 0   ┆ 0   ┆ 0   │
│ 2022091901_108 ┆ 3       ┆ 2   ┆ 1   ┆ … ┆ 1   ┆ 0   ┆ 0   ┆ 0   │
│ 2022091901_108 ┆ 4       ┆ 2   ┆ 1   ┆ … ┆ 1   ┆ 0   ┆ 0   ┆ 0   │
└────────────────┴─────────┴─────┴─────┴───┴─────┴─────┴─────┴─────┘

In [561]:
c = [
            pl.col("Id"),
            pl.col("frameId"),
            pl.col("quarter"),
            pl.col("down"),
            pl.col("yardsToGo"),
            pl.col("def"),
            pl.col("gameClock")
        ]
# score difference calculation 
team_score = presnap.select(c + [ pl.col("homeTeamAbbr"), pl.col("visitorTeamAbbr"), pl.col("preSnapHomeScore"), pl.col("preSnapVisitorScore"), pl.col("club")])
team_score = team_score.with_columns(
    scoreDiff=pl.when(pl.col("club") == pl.col("homeTeamAbbr"))
        .then(pl.col("preSnapHomeScore") - pl.col("preSnapVisitorScore"))
        .otherwise(pl.col("preSnapVisitorScore") - pl.col("preSnapHomeScore"))
)
team_score = team_score.unique(maintain_order=True)

In [562]:
result = number_of_players_per_pos.join(
    team_score,
    on=['Id', 'frameId'],
    how='left'  # Using left join to maintain the structure of team_score
).unique(maintain_order=True)
c = [
            pl.col("Id"),
            pl.col("frameId"),
            pl.col("quarter"),
            pl.col("down"),
            pl.col("yardsToGo"),
            pl.col("def"),
            pl.col("gameClock"),
            pl.col("scoreDiff"), #im stupid
"G", "C", "WR", "T", "QB", "RB", "TE", "ILB", "DT", "CB", "DE", "SS", "NT", "FS", "FB", "OLB", "MLB", "DB", "LB"
        ]
context_table = result.select(c )

In [563]:
context_table

shape: (406_816, 27)
┌────────────────┬─────────┬─────────┬──────┬───┬─────┬─────┬─────┬─────┐
│ Id             ┆ frameId ┆ quarter ┆ down ┆ … ┆ OLB ┆ MLB ┆ DB  ┆ LB  │
│ ---            ┆ ---     ┆ ---     ┆ ---  ┆   ┆ --- ┆ --- ┆ --- ┆ --- │
│ str            ┆ i64     ┆ i64     ┆ i64  ┆   ┆ u32 ┆ u32 ┆ u32 ┆ u32 │
╞════════════════╪═════════╪═════════╪══════╪═══╪═════╪═════╪═════╪═════╡
│ 2022090800_1   ┆ 76      ┆ 1       ┆ 1    ┆ … ┆ 0   ┆ 0   ┆ 0   ┆ 0   │
│ 2022090800_1   ┆ 76      ┆ 1       ┆ 1    ┆ … ┆ 0   ┆ 0   ┆ 0   ┆ 0   │
│ 2022090800_1   ┆ 77      ┆ 1       ┆ 1    ┆ … ┆ 0   ┆ 0   ┆ 0   ┆ 0   │
│ 2022090800_1   ┆ 77      ┆ 1       ┆ 1    ┆ … ┆ 0   ┆ 0   ┆ 0   ┆ 0   │
│ 2022090800_1   ┆ 78      ┆ 1       ┆ 1    ┆ … ┆ 0   ┆ 0   ┆ 0   ┆ 0   │
│ …              ┆ …       ┆ …       ┆ …    ┆ … ┆ …   ┆ …   ┆ …   ┆ …   │
│ 2022091901_108 ┆ 2       ┆ 4       ┆ 1    ┆ … ┆ 1   ┆ 0   ┆ 0   ┆ 0   │
│ 2022091901_108 ┆ 3       ┆ 4       ┆ 1    ┆ … ┆ 1   ┆ 0   ┆ 0   ┆ 0   │
│ 2022091901_108 ┆ 3       ┆ 4       ┆ 1    ┆ … ┆ 1   ┆ 0   ┆ 0   ┆ 0   │
│ 2022091901_108 ┆ 4       ┆ 4       ┆ 1    ┆ … ┆ 1   ┆ 0   ┆ 0   ┆ 0   │
│ 2022091901_108 ┆ 4       ┆ 4       ┆ 1    ┆ … ┆ 1   ┆ 0   ┆ 0   ┆ 0   │
└────────────────┴─────────┴─────────┴──────┴───┴─────┴─────┴─────┴─────┘

In [447]:
# c = [
#             pl.col("Id"),
#             pl.col("frameId"),
#             pl.col("quarter"),
#             pl.col("down"),
#             pl.col("yardsToGo"),
#             pl.col("def"),
#             pl.col("gameClock")
#         ]

# t = (
#     number_of_players_per_pos.join(
#         presnap.select(c).unique(),
#         on=["Id", "frameId"]
#     ) #two instances of 123 
# )

# final_table = t.join(
#     team_score.select(["Id", "frameId", "scoreDiff"]), 
#     on=["Id", "frameId"],
#     how="left"
# )
# context_table = final_table.unique(maintain_order=True)


# play tensor

In [564]:
col = [  'Id', 'frameId', 'position', 
'def', # are they a defensive player (based on their club)
 'x','y', #position on field (in yards)
 's', #speed of player 
 'a', #acceleration of player
 'dis', #distance from previous time point IF SKIPPING FRAMES NEED TO TALLY UP DISTANCE TRAVELLED BETWEEN FRAMES
 'o', # orientation (0 degrees is facing the sideline)
 'dir', #angle of player motion 
 #'event', # unique values: snap_direct, line_set, shift, man in motion, ball snap, null --> does not specify who is in motion: Use cayden and justin's feature for this
 #'pff_passCoverage', #specific pass coverage by defenese (cover 1, goal line, quarters, red zone, cover 0, cover 6, 2 man, cover 2, cover 3) 
 #'pff_manZone', #other, man or zone coverage (OTHER PLAYS CAN BE DROPPED FOR NOW
  'playDirection', #direction offense is moving (for yards to go calculation)
 'absoluteYardlineNumber'# used for x_los calculation
   ]
play_table = presnap.select(col) 

In [565]:
play_table.filter(pl.col('Id') == "2022091901_111")
#calculate the x_los as 120 - absoluteYardlineNumber 
play_table = play_table.with_columns(
    los=pl.when(pl.col("playDirection") == "left")
        .then(120 - pl.col("absoluteYardlineNumber"))  # If going left, LOS is (120 - yards from possession endzone)
        .otherwise(pl.col("absoluteYardlineNumber"))   # If going right, LOS is yards from possession endzone
)

play_table = play_table.with_columns(
    x_los =pl.col("los") - pl.col("x")
)
col_to_drop = ['los', 'playDirection', 'absoluteYardlineNumber'] #drop passCoverage for now
play_table = play_table.drop(col_to_drop)


In [566]:
play_table

shape: (4_474_976, 12)
┌────────────────┬─────────┬──────────┬───────┬───┬──────┬────────┬────────┬────────┐
│ Id             ┆ frameId ┆ position ┆ def   ┆ … ┆ dis  ┆ o      ┆ dir    ┆ x_los  │
│ ---            ┆ ---     ┆ ---      ┆ ---   ┆   ┆ ---  ┆ ---    ┆ ---    ┆ ---    │
│ str            ┆ i64     ┆ str      ┆ bool  ┆   ┆ f64  ┆ f64    ┆ f64    ┆ f64    │
╞════════════════╪═════════╪══════════╪═══════╪═══╪══════╪════════╪════════╪════════╡
│ 2022090800_1   ┆ 76      ┆ G        ┆ false ┆ … ┆ 0.01 ┆ 80.73  ┆ 103.68 ┆ 1.02   │
│ 2022090800_1   ┆ 76      ┆ C        ┆ false ┆ … ┆ 0.01 ┆ 77.55  ┆ 75.61  ┆ 0.46   │
│ 2022090800_1   ┆ 76      ┆ WR       ┆ false ┆ … ┆ 0.45 ┆ 164.97 ┆ 182.51 ┆ 2.02   │
│ 2022090800_1   ┆ 76      ┆ T        ┆ false ┆ … ┆ 0.01 ┆ 74.87  ┆ 10.26  ┆ 0.99   │
│ 2022090800_1   ┆ 76      ┆ WR       ┆ false ┆ … ┆ 0.01 ┆ 80.46  ┆ 55.32  ┆ 1.26   │
│ …              ┆ …       ┆ …        ┆ …     ┆ … ┆ …    ┆ …      ┆ …      ┆ …      │
│ 2022091901_108 ┆ 4       ┆ SS       ┆ true  ┆ … ┆ 0.07 ┆ 276.49 ┆ 142.51 ┆ -16.15 │
│ 2022091901_108 ┆ 4       ┆ ILB      ┆ true  ┆ … ┆ 0.03 ┆ 263.01 ┆ 46.14  ┆ -5.21  │
│ 2022091901_108 ┆ 4       ┆ CB       ┆ true  ┆ … ┆ 0.04 ┆ 252.98 ┆ 256.74 ┆ -4.91  │
│ 2022091901_108 ┆ 4       ┆ CB       ┆ true  ┆ … ┆ 0.02 ┆ 291.56 ┆ 93.76  ┆ -5.89  │
│ 2022091901_108 ┆ 4       ┆ OLB      ┆ true  ┆ … ┆ 0.03 ┆ 222.12 ┆ 246.45 ┆ -0.47  │
└────────────────┴─────────┴──────────┴───────┴───┴──────┴────────┴────────┴────────┘

# make the tensor


encoding ordinal features


In [631]:
label_table.select(pl.col('pff_manZone')).describe()

shape: (9, 2)
┌────────────┬─────────────┐
│ statistic  ┆ pff_manZone │
│ ---        ┆ ---         │
│ str        ┆ str         │
╞════════════╪═════════════╡
│ count      ┆ 203408      │
│ null_count ┆ 0           │
│ mean       ┆ null        │
│ std        ┆ null        │
│ min        ┆ Man         │
│ 25%        ┆ null        │
│ 50%        ┆ null        │
│ 75%        ┆ null        │
│ max        ┆ Zone        │
└────────────┴─────────────┘

In [632]:
def man_or_zone(str):
    if str == 'Man':
        return 0
    else:
        return 1
encoded_label_table = label_table.with_columns(
    pl.col('pff_manZone').map_elements(man_or_zone, return_dtype=pl.Int32).alias('pff_manZone')
)

In [640]:
encoded_label_table.filter(pl.col('Id') == play_id).select(pl.col('pff_manZone')).to_series().last()

1

In [567]:
mapping = {
    'quarter': {1: 0, 2: 1, 3: 2, 4: 3},
    'down': {1: 0, 2: 1, 3: 2, 4: 3}
}

def time_to_seconds(time_str):
    minutes, seconds = map(int, time_str.strip('"').split(':'))
    return minutes * 60 + seconds

encoded_context_table = context_table.with_columns([
    # Gameclock
    pl.col('gameClock').map_elements(time_to_seconds, return_dtype=pl.Int32).alias('gameClock'),
    
    # Quarter - using mapping
    pl.col('quarter').map_elements(lambda x: mapping['quarter'][x], return_dtype=pl.Int32).alias('quarter'),
    
    # Down - using mapping
    pl.col('down').map_elements(lambda x: mapping['down'][x], return_dtype=pl.Int32).alias('down')
])

# No need to drop columns since we're overwriting them instead of creating new ones
encoded_context_table

shape: (406_816, 27)
┌────────────────┬─────────┬─────────┬──────┬───┬─────┬─────┬─────┬─────┐
│ Id             ┆ frameId ┆ quarter ┆ down ┆ … ┆ OLB ┆ MLB ┆ DB  ┆ LB  │
│ ---            ┆ ---     ┆ ---     ┆ ---  ┆   ┆ --- ┆ --- ┆ --- ┆ --- │
│ str            ┆ i64     ┆ i32     ┆ i32  ┆   ┆ u32 ┆ u32 ┆ u32 ┆ u32 │
╞════════════════╪═════════╪═════════╪══════╪═══╪═════╪═════╪═════╪═════╡
│ 2022090800_1   ┆ 76      ┆ 0       ┆ 0    ┆ … ┆ 0   ┆ 0   ┆ 0   ┆ 0   │
│ 2022090800_1   ┆ 76      ┆ 0       ┆ 0    ┆ … ┆ 0   ┆ 0   ┆ 0   ┆ 0   │
│ 2022090800_1   ┆ 77      ┆ 0       ┆ 0    ┆ … ┆ 0   ┆ 0   ┆ 0   ┆ 0   │
│ 2022090800_1   ┆ 77      ┆ 0       ┆ 0    ┆ … ┆ 0   ┆ 0   ┆ 0   ┆ 0   │
│ 2022090800_1   ┆ 78      ┆ 0       ┆ 0    ┆ … ┆ 0   ┆ 0   ┆ 0   ┆ 0   │
│ …              ┆ …       ┆ …       ┆ …    ┆ … ┆ …   ┆ …   ┆ …   ┆ …   │
│ 2022091901_108 ┆ 2       ┆ 3       ┆ 0    ┆ … ┆ 1   ┆ 0   ┆ 0   ┆ 0   │
│ 2022091901_108 ┆ 3       ┆ 3       ┆ 0    ┆ … ┆ 1   ┆ 0   ┆ 0   ┆ 0   │
│ 2022091901_108 ┆ 3       ┆ 3       ┆ 0    ┆ … ┆ 1   ┆ 0   ┆ 0   ┆ 0   │
│ 2022091901_108 ┆ 4       ┆ 3       ┆ 0    ┆ … ┆ 1   ┆ 0   ┆ 0   ┆ 0   │
│ 2022091901_108 ┆ 4       ┆ 3       ┆ 0    ┆ … ┆ 1   ┆ 0   ┆ 0   ┆ 0   │
└────────────────┴─────────┴─────────┴──────┴───┴─────┴─────┴─────┴─────┘

In [568]:
vectorizer = kr.TableVectorizer(    specific_transformers=[
        ("passthrough", ["Id", "frameId"])  
    ])
encoded_play_table = vectorizer.fit_transform(play_table)
encoded_play_table

shape: (4_474_976, 30)
┌───────────────┬─────────┬────────────┬─────────────┬───┬──────┬────────────┬────────────┬────────┐
│ Id            ┆ frameId ┆ position_C ┆ position_CB ┆ … ┆ dis  ┆ o          ┆ dir        ┆ x_los  │
│ ---           ┆ ---     ┆ ---        ┆ ---         ┆   ┆ ---  ┆ ---        ┆ ---        ┆ ---    │
│ str           ┆ i64     ┆ f32        ┆ f32         ┆   ┆ f32  ┆ f32        ┆ f32        ┆ f32    │
╞═══════════════╪═════════╪════════════╪═════════════╪═══╪══════╪════════════╪════════════╪════════╡
│ 2022090800_1  ┆ 76      ┆ 0.0        ┆ 0.0         ┆ … ┆ 0.01 ┆ 80.730003  ┆ 103.68     ┆ 1.02   │
│ 2022090800_1  ┆ 76      ┆ 1.0        ┆ 0.0         ┆ … ┆ 0.01 ┆ 77.550003  ┆ 75.610001  ┆ 0.46   │
│ 2022090800_1  ┆ 76      ┆ 0.0        ┆ 0.0         ┆ … ┆ 0.45 ┆ 164.970001 ┆ 182.509995 ┆ 2.02   │
│ 2022090800_1  ┆ 76      ┆ 0.0        ┆ 0.0         ┆ … ┆ 0.01 ┆ 74.870003  ┆ 10.26      ┆ 0.99   │
│ 2022090800_1  ┆ 76      ┆ 0.0        ┆ 0.0         ┆ … ┆ 0.01 ┆ 80.459999  ┆ 55.32      ┆ 1.26   │
│ …             ┆ …       ┆ …          ┆ …           ┆ … ┆ …    ┆ …          ┆ …          ┆ …      │
│ 2022091901_10 ┆ 4       ┆ 0.0        ┆ 0.0         ┆ … ┆ 0.07 ┆ 276.48999  ┆ 142.509995 ┆ -16.15 │
│ 8             ┆         ┆            ┆             ┆   ┆      ┆            ┆            ┆        │
│ 2022091901_10 ┆ 4       ┆ 0.0        ┆ 0.0         ┆ … ┆ 0.03 ┆ 263.01001  ┆ 46.139999  ┆ -5.21  │
│ 8             ┆         ┆            ┆             ┆   ┆      ┆            ┆            ┆        │
│ 2022091901_10 ┆ 4       ┆ 0.0        ┆ 1.0         ┆ … ┆ 0.04 ┆ 252.979996 ┆ 256.73999  ┆ -4.91  │
│ 8             ┆         ┆            ┆             ┆   ┆      ┆            ┆            ┆        │
│ 2022091901_10 ┆ 4       ┆ 0.0        ┆ 1.0         ┆ … ┆ 0.02 ┆ 291.559998 ┆ 93.760002  ┆ -5.89  │
│ 8             ┆         ┆            ┆             ┆   ┆      ┆            ┆            ┆        │
│ 2022091901_10 ┆ 4       ┆ 0.0        ┆ 0.0         ┆ … ┆ 0.03 ┆ 222.119995 ┆ 246.449997 ┆ -0.47  │
│ 8             ┆         ┆            ┆             ┆   ┆      ┆            ┆            ┆        │
└───────────────┴─────────┴────────────┴─────────────┴───┴──────┴────────────┴────────────┴────────┘

In [569]:
encoded_context_features = [col for col in encoded_context_table.columns if col not in ['Id', 'frameId']]
encoded_context_features_len = len(encoded_context_features)
encoded_play_features = [col for col in encoded_play_table.columns if col not in ['Id', 'frameId']]
encoded_play_features_len = len(encoded_play_features)

In [570]:
#lets look at it from the offense perspective 
encoded_context_table = encoded_context_table.filter(pl.col('def') == False)

In [571]:
# For each column
for col in frame_players.columns:
    # Get the first array's length in that column
    first_array_length = len(frame_players[0, col].to_list())
    print(f"Column {col}: First array length = {first_array_length}")
    
    # Let's verify if all arrays in this column have the same length
    all_lengths = [len(arr.to_list()) for arr in frame_players[col]]
    if len(set(all_lengths)) > 1:
        print(f"Warning: Not all arrays in {col} have the same length!")
        print(f"Found lengths: {set(all_lengths)}")

Column position_C: First array length = 22
Column position_CB: First array length = 22
Column position_DB: First array length = 22
Column position_DE: First array length = 22
Column position_DT: First array length = 22
Column position_FB: First array length = 22
Column position_FS: First array length = 22
Column position_G: First array length = 22
Column position_ILB: First array length = 22
Column position_LB: First array length = 22
Column position_MLB: First array length = 22
Column position_NT: First array length = 22
Column position_OLB: First array length = 22
Column position_QB: First array length = 22
Column position_RB: First array length = 22
Column position_SS: First array length = 22
Column position_T: First array length = 22
Column position_TE: First array length = 22
Column position_WR: First array length = 22
Column def: First array length = 22
Column x: First array length = 22
Column y: First array length = 22
Column s: First array length = 22
Column a: First array leng

In [626]:
label_table

shape: (212_214, 4)
┌────────────────┬─────────┬─────────────┬──────────────────┐
│ Id             ┆ frameId ┆ pff_manZone ┆ pff_passCoverage │
│ ---            ┆ ---     ┆ ---         ┆ ---              │
│ str            ┆ i64     ┆ str         ┆ str              │
╞════════════════╪═════════╪═════════════╪══════════════════╡
│ 2022090800_1   ┆ 76      ┆ Zone        ┆ Cover-6          │
│ 2022090800_1   ┆ 77      ┆ Zone        ┆ Cover-6          │
│ 2022090800_1   ┆ 78      ┆ Zone        ┆ Cover-6          │
│ 2022090800_1   ┆ 79      ┆ Zone        ┆ Cover-6          │
│ 2022090800_1   ┆ 80      ┆ Zone        ┆ Cover-6          │
│ …              ┆ …       ┆ …           ┆ …                │
│ 2022091901_111 ┆ 75      ┆ Other       ┆ Red Zone         │
│ 2022091901_111 ┆ 76      ┆ Other       ┆ Red Zone         │
│ 2022091901_111 ┆ 77      ┆ Other       ┆ Red Zone         │
│ 2022091901_111 ┆ 78      ┆ Other       ┆ Red Zone         │
│ 2022091901_111 ┆ 79      ┆ Other       ┆ Red Zone         │
└────────────────┴─────────┴─────────────┴──────────────────┘

In [659]:
encoded_label_table.filter(pl.col('Id') == '2022090800_109')
label_array = encoded_label_table.filter(pl.col('Id') == play_id).select(pl.col('pff_manZone')).to_series().last()
label_array
torch.FloatTensor([label_array])

tensor([1.])

In [660]:
play_tensors = {}

play_ids = encoded_context_table.select('Id').unique(maintain_order=True).to_series().to_list()

for play_id in play_ids:
    play_frames = encoded_context_table.filter(pl.col("Id") == play_id).select('frameId').unique(maintain_order=True).to_series().to_list() # If you want to have both perspectives of teh offense and defense context, this should be *2 
    
    num_frames = len(play_frames)
    context_array = np.zeros((num_frames, encoded_context_features_len)) 
    context_features = encoded_context_table.filter((pl.col('Id') == play_id)).sort('frameId').select(encoded_context_features).to_numpy()
    context_array[:len(context_features)] = context_features
    
    label_array = encoded_label_table.filter(pl.col('Id') == play_id).select(pl.col('pff_manZone')).to_series().last()

    play_array = np.zeros((num_frames, 22, encoded_play_features_len))
    frame_players = (encoded_play_table.filter((pl.col('Id') == play_id)).sort('frameId').group_by('frameId', maintain_order=True)
        .agg([pl.all().exclude(['Id', 'frameId'])]).select(pl.all().exclude('frameId'))  #group for each frame of the play, and then on each frame aggregate the player features into an array 
    )
    frame_players_3d = np.stack(frame_players.to_numpy().tolist()).reshape(num_frames, 22, encoded_play_features_len) #71 frames 28 features 22 players

    play_array = frame_players_3d.reshape(num_frames, 22, encoded_play_features_len)
    
    play_tensors[play_id] = {
        'context_tensor': torch.FloatTensor(context_array),
        'player_tensor': torch.FloatTensor(play_array),
        'label':torch.FloatTensor([label_array])
    }

    #takes like 3:30 to run 

In [697]:
torch.save(play_tensors, 'play_tensors.pt')

In [661]:
encoded_label_table.filter(pl.col("Id") == '2022090800_1').select('pff_manZone').to_series().last()

1

In [662]:
play_tensors['2022090800_1']['label']

tensor([1.])

In [644]:
encoded_label_table.filter(pl.col('Id') == '2022090800_1')

shape: (71, 4)
┌──────────────┬─────────┬─────────────┬──────────────────┐
│ Id           ┆ frameId ┆ pff_manZone ┆ pff_passCoverage │
│ ---          ┆ ---     ┆ ---         ┆ ---              │
│ str          ┆ i64     ┆ i32         ┆ str              │
╞══════════════╪═════════╪═════════════╪══════════════════╡
│ 2022090800_1 ┆ 76      ┆ 1           ┆ Cover-6          │
│ 2022090800_1 ┆ 77      ┆ 1           ┆ Cover-6          │
│ 2022090800_1 ┆ 78      ┆ 1           ┆ Cover-6          │
│ 2022090800_1 ┆ 79      ┆ 1           ┆ Cover-6          │
│ 2022090800_1 ┆ 80      ┆ 1           ┆ Cover-6          │
│ …            ┆ …       ┆ …           ┆ …                │
│ 2022090800_1 ┆ 142     ┆ 1           ┆ Cover-6          │
│ 2022090800_1 ┆ 143     ┆ 1           ┆ Cover-6          │
│ 2022090800_1 ┆ 144     ┆ 1           ┆ Cover-6          │
│ 2022090800_1 ┆ 145     ┆ 1           ┆ Cover-6          │
│ 2022090800_1 ┆ 146     ┆ 1           ┆ Cover-6          │
└──────────────┴─────────┴─────────────┴──────────────────┘

# start model

data loader

In [726]:
# what u currently ahve 
play_tensors #Each play id has an associated context tensor, player tensor, and label tensor 

print(play_tensors['2022090800_1']['context_tensor'].shape)
print(play_tensors['2022090800_1']['player_tensor'].shape)
print(play_tensors['2022090800_1']['label'].shape)


torch.Size([71, 25])
torch.Size([71, 22, 28])
torch.Size([1])


train test split

In [771]:
encoded_context_features_len

25

In [762]:
from sklearn.model_selection import train_test_split

play_ids = list(play_tensors.keys())
train_val_ids, test_ids = train_test_split(
    play_ids, 
    test_size=0.2, 
    random_state=42
)
train_ids, val_ids = train_test_split(
    train_val_ids,
    test_size=0.2,
    random_state=42
)

#split play_tensors into 3 sets
train_tensors = {play_id: play_tensors[play_id] for play_id in train_ids}
val_tensors = {play_id: play_tensors[play_id] for play_id in val_ids}
test_tensors = {play_id: play_tensors[play_id] for play_id in test_ids}

In [841]:
type(batch['labels'])

list

In [777]:
from torch.utils.data import Dataset, DataLoader
from torch.nn.utils.rnn import pad_sequence
import torch.nn.utils.rnn as rnn_utils

class CoverageDataset(Dataset):
    def __init__(self, tensors):
        self.tensors = tensors #store play_tensors 
        self.play_ids = list(tensors.keys()) #store play_ids
        
    def __len__(self):
        return len(self.play_ids)
    
    def __getitem__(self, idx):
        play_id = self.play_ids[idx]
        
        context_tensor = self.tensors[play_id]['context_tensor'] 
        player_tensor = self.tensors[play_id]['player_tensor']
        label = self.tensors[play_id]['label']
        
        return {
            'play_id': play_id,
            'context_data': context_tensor,
            'play_data': player_tensor,
            'label': label
        }
    
def collate_fn(batch):
    # Sort batch by sequence length in descending order
    batch.sort(key=lambda x: x['play_data'].shape[0], reverse=True)
    
    play_data = [item['play_data'] for item in batch]
    context_data = [item['context_data'] for item in batch]
    play_ids = [item['play_id'] for item in batch]
    labels = [item['label'] for item in batch]

    lengths = torch.tensor([len(x) for x in play_data])
    
    # Pad sequences
    play_data_padded = rnn_utils.pad_sequence(play_data, batch_first=True)
    context_data_padded = rnn_utils.pad_sequence(context_data, batch_first=True)
    return {
        'play_ids': play_ids,
        'play_data': play_data_padded,
        'context_data': context_data_padded,
        'lengths': lengths,
        'labels': labels  
    }

def prepare_dataloader(play_dict, batch_size=32, shuffle=False):
    dataset = CoverageDataset(play_dict)
    dataloader = DataLoader(
        dataset, 
        batch_size=batch_size, 
        shuffle=shuffle, 
        collate_fn=collate_fn
    )

    return dataloader

In [779]:
train_loader = prepare_dataloader(train_tensors, batch_size=32, shuffle=False)
val_loader = prepare_dataloader(val_tensors, batch_size=32, shuffle=False)

model architecture 

In [836]:
import torch
import torch.nn as nn
import torch.nn.functional as F

class LSTMCoveragePred(nn.Module):
    def __init__(self,hidden_size_play=256, hidden_size_context=128, num_classes=2):
        super().__init__()
        self.hidden_size_play = hidden_size_play
        self.hidden_size_context = hidden_size_context
    
        self.play_features_size = 22 * encoded_play_features_len
        self.context_features_size = encoded_context_features_len

        self.play_lstm = nn.LSTM(input_size=self.play_features_size, hidden_size=self.hidden_size_play, batch_first=True)
        self.context_lstm = nn.LSTM(input_size=self.context_features_size, hidden_size=hidden_size_context, batch_first=True)    
        self.attention = nn.MultiheadAttention(embed_dim=hidden_size_play, num_heads=8, batch_first=True)

        self.prediction_layer = nn.Sequential(
                nn.Linear(hidden_size_play + hidden_size_context, hidden_size_context),
                nn.ReLU(),
                nn.Dropout(0.1),
                nn.Linear(hidden_size_context, 1))
        
    def create_causal_mask(self, seq_len, device): # only look at past frames unid-rectional attention 
       mask = torch.triu(torch.ones(seq_len, seq_len), diagonal=1).bool()
       return mask.to(device)   
    
    def forward(self, play_tensor, context_tensor, lengths):
        batch_size = play_tensor.size(0)
        seq_len = play_tensor.size(1)
        
        # Reshape play tensor to combine players and features
        # From: (batch, seq, players, features) -> (batch, seq, players*features)
        play_tensor = play_tensor.reshape(batch_size, seq_len,  self.play_features_size)  # Becomes (batch, 144, 616)
        context_tensor = context_tensor # no need to flatten

        # Pack sequences for both play and context
        play_packed = nn.utils.rnn.pack_padded_sequence(play_tensor, lengths, batch_first=True, enforce_sorted=False)
        context_packed = nn.utils.rnn.pack_padded_sequence(context_tensor, lengths, batch_first=True, enforce_sorted=False)
        
        # Pass through LSTMs
        play_output, _ = self.play_lstm(play_packed)  
        context_output, _ = self.context_lstm(context_packed)
        
        # Unpack sequences
        play_output, _ = nn.utils.rnn.pad_packed_sequence(play_output, batch_first=True)  # (batch, seq, hidden_size_play)
        context_output, _ = nn.utils.rnn.pad_packed_sequence(context_output, batch_first=True)  # (batch, seq, hidden_size_context)
        
        # Apply attention
        attn_mask = self.create_causal_mask(play_tensor.size(1), play_tensor.device)
        play_attended, _ = self.attention(play_output, play_output, play_output, 
                                        attn_mask=attn_mask, need_weights=False)
        
        # Combine features
        combined = torch.cat([play_attended, context_output], dim=-1)  # (batch, seq, hidden_size_play + hidden_size_context)
        
        # Make predictions
        predictions = self.prediction_layer(combined)  # (batch, seq, 2)
        pred_probs = torch.sigmoid(predictions)  # Apply softmax over last dimension
        
        return predictions, pred_probs, predictions.shape

train

In [846]:
import torch.optim as optim
from tqdm import tqdm

model = LSTMCoveragePred(hidden_size_play=256, hidden_size_context=128, num_classes=2)
optimizer = optim.Adam(model.parameters(), lr=0.001)
criterion = nn.CrossEntropyLoss()
num_epochs = 100
device = torch.device('mps' if torch.backends.mps.is_available() else 'cpu')
print(f'Using device: {device}')
model = model.to(device)
best_model = None
best_val_loss = float('inf')

for epoch in range(num_epochs):
    model.train()
    running_loss = 0.0

    for batch in train_loader: 
        play_data = batch['play_data'].to(device)
        context_data = batch['context_data'].to(device)
        labels = torch.stack(batch['labels']).to(device)
        lengths = batch['lengths']


        optimizer.zero_grad()

        predictions, proba, fye = model(play_data, context_data, lengths)

        #loss = criterion(predictions.reshape(-1, 2), labels.reshape(-1))
        loss = criterion(predictions, labels.long())
        loss.backward()
        optimizer.step()
        running_loss += loss.item()
    epoch_loss = running_loss/len(train_loader)
    print(f'Epoch {epoch+1}, Loss: {epoch_loss:.4f}')

    #validate
    val_loss = 0.0
    with torch.no_grad():
        for batch in val_loader:
            play_data = batch['play_data'].to(device)
            context_data = batch['context_data'].to(device)
            labels = torch.stack(batch['labels']).to(device)
            lengths = batch['lengths']

            predictions, proba,fye = model(play_data, context_data, lengths)
            loss = criterion(predictions, labels.long())
            val_loss += loss.item()
    
    val_loss /= len(val_loader)
    if val_loss < best_val_loss:
        best_val_loss = val_loss
        best_model = model.state_dict().copy()


Using device: mps
Epoch 1, Loss: 4.9542
Epoch 2, Loss: 4.9639
Epoch 3, Loss: 4.9639
Epoch 4, Loss: 4.9639
Epoch 5, Loss: 4.9639
Epoch 6, Loss: 4.9639
Epoch 7, Loss: 4.9639
Epoch 8, Loss: 4.9639
Epoch 9, Loss: 4.9639
Epoch 10, Loss: 4.9639
Epoch 11, Loss: 4.9639
Epoch 12, Loss: 4.9639
Epoch 13, Loss: 4.9639
Epoch 14, Loss: 4.9639
Epoch 15, Loss: 4.9639
Epoch 16, Loss: 4.9639
Epoch 17, Loss: 4.9639
Epoch 18, Loss: 4.9639
Epoch 19, Loss: 4.9639
Epoch 20, Loss: 4.9639
Epoch 21, Loss: 4.9639
Epoch 22, Loss: 4.9639
Epoch 23, Loss: 4.9639


KeyboardInterrupt: 

tensor([[1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1.0662],
        [1

8000

In [720]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(f"Using device: {device}")
model = LSTMCoveragePred()
trained_model, history = train_model(
    model=model,
    train_loader=train_loader,
    val_loader=val_loader,
    num_epochs=50,
    learning_rate=0.001,
    device=device,  
    patience=5
)

Using device: cpu

Epoch 1/50


KeyboardInterrupt: 

In [707]:
print("Play data shape:", play_data.shape)
print("Context data shape:", context_data.shape)
print("Play features size:", model.play_features_size)
print("Context features size:", model.context_features_size)

Play data shape: torch.Size([32, 144, 22, 28])
Context data shape: torch.Size([32, 144, 25])
Play features size: 616
Context features size: 25


# shit

In [679]:
import torch
import torch.nn as nn
import torch.nn.functional as F
class LSTMPredModel(nn.Module):
   def __init__(self, hidden_size_players=256, hidden_size_context=128, num_classes=2):
       super().__init__()
       
       # Previous layers (LSTMs and Attention)
       self.player_lstm = nn.LSTM(input_size=22*encoded_play_features_len, hidden_size=hidden_size_players, batch_first=True)
       self.context_lstm = nn.LSTM(input_size=25, hidden_size=hidden_size_context, batch_first=True)
       self.player_attention = nn.MultiheadAttention(embed_dim=hidden_size_players, num_heads=8, batch_first=True)
       
       # Feature combination
       self.final_projection = nn.Linear(hidden_size_players + hidden_size_context, hidden_size_players)
       
       # Prediction head
       self.prediction_layers = nn.Sequential(
           nn.Linear(hidden_size_players, hidden_size_players//2),
           nn.ReLU(),
           nn.Dropout(0.1),
           nn.Linear(hidden_size_players//2, num_classes)
       )

   def create_causal_mask(self, seq_len, device): # only look at past frames unid-rectional attention 
       mask = torch.triu(torch.ones(seq_len, seq_len), diagonal=1).bool()
       return mask.to(device)

   def forward(self, play_data, context_data, lengths):
       batch_size = play_data.size(0)
       seq_len = play_data.size(1)
       
       # Previous processing (LSTMs and Attention)
       play_flattened = play_data.reshape(batch_size, -1, 22*encoded_play_features_len)
       
       play_packed = nn.utils.rnn.pack_padded_sequence(play_flattened, lengths, batch_first=True, enforce_sorted=False)
       context_packed = nn.utils.rnn.pack_padded_sequence(context_data, lengths, batch_first=True, enforce_sorted=False)
       
       player_out, _ = self.player_lstm(play_packed)
       context_out, _ = self.context_lstm(context_packed)
       
       player_out, _ = nn.utils.rnn.pad_packed_sequence(player_out, batch_first=True)
       context_out, _ = nn.utils.rnn.pad_packed_sequence(context_out, batch_first=True)
       
       # Attention
       attn_mask = self.create_causal_mask(seq_len, play_data.device)
       player_attended, _ = self.player_attention(player_out, player_out, player_out, attn_mask=attn_mask, need_weights=False)
       
       # Combine features
       combined = torch.cat([player_attended, context_out], dim=-1)
       projected = self.final_projection(combined)
       
       # Get the final frame's features for prediction
       
       # Make prediction
       predictions = self.prediction_layers(projected)
       
       return predictions, pred_probs

In [680]:
from torch.utils.data import Dataset, DataLoader
import torch.nn.utils.rnn as rnn_utils

class DatasetLoad(Dataset):
    def __init__(self, play_dict):
        self.play_ids = list(play_dict.keys())
        self.play_dict = play_dict

    def __len__(self):
        return len(self.play_ids)

    def __getitem__(self, idx):
        play_id = self.play_ids[idx]
        context_tensor = self.play_dict[play_id]['context_tensor']
        player_tensor = self.play_dict[play_id]['player_tensor']
        label = self.play_dict[play_id]['label']
        
        return {
            'play_id': play_id,
            'context_data': context_tensor,
            'play_data': player_tensor,
            'label': label
        }
    

def collate_fn(batch):
    # Sort batch by sequence length in descending order
    batch.sort(key=lambda x: x['play_data'].shape[0], reverse=True)
    
    # Extract tensors
    play_data = [item['play_data'] for item in batch]
    context_data = [item['context_data'] for item in batch]
    play_ids = [item['play_id'] for item in batch]
    labels = torch.tensor([item['label'].item() for item in batch], dtype=torch.long)

    # Get lengths
    lengths = torch.tensor([len(x) for x in play_data])
    
    # Pad sequences
    play_data_padded = rnn_utils.pad_sequence(play_data, batch_first=True)
    context_data_padded = rnn_utils.pad_sequence(context_data, batch_first=True)
    
    return {
        'play_ids': play_ids,
        'play_data': play_data_padded,
        'context_data': context_data_padded,
        'lengths': lengths,
        'labels': labels  
    }

def prepare_dataloader(play_dict, batch_size=32, shuffle=False):
    dataset = DatasetLoad(play_dict)
    dataloader = DataLoader(
        dataset, 
        batch_size=batch_size, 
        shuffle=shuffle, 
        collate_fn=collate_fn
    )
    return dataloader

In [681]:
from sklearn.model_selection import train_test_split

from sklearn.model_selection import train_test_split

def split_play_dict(play_dict, train_size=0.7, val_size=0.15, test_size=0.15, random_state=42):
    """
    Split the play dictionary into train, validation, and test dictionaries
    """
    # Get all play IDs
    play_ids = list(play_dict.keys())
    
    # First split: separate training set
    train_ids, temp_ids = train_test_split(
        play_ids,
        train_size=train_size,
        random_state=random_state
    )
    
    # Second split: separate validation and test from the remaining data
    val_ids, test_ids = train_test_split(
        temp_ids,
        test_size=test_size/(test_size + val_size),
        random_state=random_state
    )
    
    # Create separate dictionaries
    train_dict = {play_id: play_dict[play_id] for play_id in train_ids}
    val_dict = {play_id: play_dict[play_id] for play_id in val_ids}
    test_dict = {play_id: play_dict[play_id] for play_id in test_ids}
    
    print(f"Training set size: {len(train_dict)}")
    print(f"Validation set size: {len(val_dict)}")
    print(f"Test set size: {len(test_dict)}")
    
    return train_dict, val_dict, test_dict

# Usage:
train_dict, val_dict, test_dict = split_play_dict(play_tensors)

# Create DataLoaders for each split
train_loader = prepare_dataloader(train_dict, batch_size=32, shuffle=True)
val_loader = prepare_dataloader(val_dict, batch_size=32, shuffle=False)
test_loader = prepare_dataloader(test_dict, batch_size=32, shuffle=False)

Training set size: 2429
Validation set size: 521
Test set size: 521


In [686]:
import torch
import torch.nn as nn
from tqdm import tqdm
import numpy as np
from sklearn.metrics import accuracy_score, precision_recall_fscore_support

def train_model(model, train_loader, val_loader, test_loader, 
                num_epochs=50, learning_rate=0.001, device='cuda'):
    
    # Move model to device
    model = model.to(device)
    
    # Initialize optimizer and loss function
    optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate)
    criterion = nn.CrossEntropyLoss()
    
    # Track best model and metrics
    best_val_loss = float('inf')
    best_model_state = None
    
    # Training history
    history = {
        'train_loss': [], 'val_loss': [],
        'train_acc': [], 'val_acc': []
    }
    
    for epoch in range(num_epochs):
        print(f"\nEpoch {epoch+1}/{num_epochs}")
        
        # Training phase
        model.train()
        train_losses = []
        train_preds = []
        train_true = []
        
        for batch in tqdm(train_loader, desc="Training"):
            # Move batch to device
            play_data = batch['play_data'].to(device)
            context_data = batch['context_data'].to(device)
            lengths = batch['lengths']
            labels = batch['labels'].to(device)
            
            # Forward pass
            # In your training loop:
            predictions = model(play_data, context_data, lengths)
            print("Predictions shape:", predictions.shape)
            print("Labels shape:", labels.shape)
            labels = labels.squeeze()  # Try squeezing to remove extra dimensions
            print("Labels after squeeze:", labels.shape)
            loss = criterion(predictions, labels)          
            # Backward pass
            optimizer.zero_grad()
            loss.backward()
            optimizer.step()
            
            # Track metrics
            train_losses.append(loss.item())
            train_preds.extend(predictions.argmax(dim=1).cpu().numpy())
            train_true.extend(labels.cpu().numpy())
        
        # Calculate training metrics
        train_loss = np.mean(train_losses)
        train_acc = accuracy_score(train_true, train_preds)
        
        # Validation phase
        model.eval()
        val_losses = []
        val_preds = []
        val_true = []
        
        with torch.no_grad():
            for batch in tqdm(val_loader, desc="Validation"):
                # Move batch to device
                play_data = batch['play_data'].to(device)
                context_data = batch['context_data'].to(device)
                lengths = batch['lengths']
                labels = batch['labels'].to(device)
                
                # Forward pass
                predictions = model(play_data, context_data, lengths)
                loss = criterion(predictions, labels)
                
                # Track metrics
                val_losses.append(loss.item())
                val_preds.extend(predictions.argmax(dim=1).cpu().numpy())
                val_true.extend(labels.cpu().numpy())
        
        # Calculate validation metrics
        val_loss = np.mean(val_losses)
        val_acc = accuracy_score(val_true, val_preds)
        
        # Save best model
        if val_loss < best_val_loss:
            best_val_loss = val_loss
            best_model_state = model.state_dict().copy()
        
        # Update history
        history['train_loss'].append(train_loss)
        history['val_loss'].append(val_loss)
        history['train_acc'].append(train_acc)
        history['val_acc'].append(val_acc)
        
        # Print epoch metrics
        print(f"\nTrain Loss: {train_loss:.4f} | Train Acc: {train_acc:.4f}")
        print(f"Val Loss: {val_loss:.4f} | Val Acc: {val_acc:.4f}")
    
    # Load best model for testing
    model.load_state_dict(best_model_state)
    
    # Testing phase
    model.eval()
    test_preds = []
    test_true = []
    
    print("\nEvaluating on test set...")
    with torch.no_grad():
        for batch in tqdm(test_loader, desc="Testing"):
            # Move batch to device
            play_data = batch['play_data'].to(device)
            context_data = batch['context_data'].to(device)
            lengths = batch['lengths']
            labels = batch['labels'].to(device)
            
            # Forward pass
            predictions = model(play_data, context_data, lengths)
            
            # Track predictions
            test_preds.extend(predictions.argmax(dim=1).cpu().numpy())
            test_true.extend(labels.cpu().numpy())
    
    # Calculate test metrics
    test_acc = accuracy_score(test_true, test_preds)
    
    print("\nTest Set Metrics:")
    print(f"Accuracy: {test_acc:.4f}")

    
    return model, history

# Usage:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# Initialize model
model = LSTMPredModel(
    hidden_size_players=256,
    hidden_size_context=128,
    num_classes=2  # binary classification
)

# Split data and create dataloaders
train_dict, val_dict, test_dict = split_play_dict(play_tensors)
train_loader = prepare_dataloader(train_dict, batch_size=32, shuffle=True)
val_loader = prepare_dataloader(val_dict, batch_size=32, shuffle=False)
test_loader = prepare_dataloader(test_dict, batch_size=32, shuffle=False)

# Train model
model, history = train_model(
    model=model,
    train_loader=train_loader,
    val_loader=val_loader,
    test_loader=test_loader,
    num_epochs=50,
    learning_rate=0.001,
    device=device
)

Training set size: 2429
Validation set size: 521
Test set size: 521

Epoch 1/50


Training:   0%|          | 0/76 [00:00<?, ?it/s]

Predictions shape: torch.Size([32, 211, 2])
Labels shape: torch.Size([32])
Labels after squeeze: torch.Size([32])


RuntimeError: Expected target size [32, 2], got [32]

In [675]:
play_tensors['2022090800_1']['label']

tensor([1.])

In [624]:
import torch.optim as optim
import torch.nn.functional as F
from tqdm import tqdm

model = LSTMPredModel()
dataloader = prepare_dataloader(play_tensors)

optimizer = optim.Adam(model.parameters(), lr=0.001)
criterion = nn.CrossEntropyLoss()
num_epochs = 100
# Training loop
for epoch in range(num_epochs):
    model.train()
    total_loss = 0

    # Use tqdm to display a progress bar
    train_loader = tqdm(dataloader, desc=f"Epoch [{epoch+1}/{num_epochs}]", unit="batch")
    for batch in train_loader:
        optimizer.zero_grad()

        play_data = batch['play_data']
        context_data = batch['context_data']
        lengths = batch['lengths']

        # Forward pass
        output = model(play_data, context_data, lengths)

        # Compute loss
        loss = criterion(output, labels)  # Replace 'labels' with your actual target labels
        loss.backward()
        optimizer.step()

        total_loss += loss.item()

        # Update the progress bar
        train_loader.set_postfix(loss=total_loss / (i+1))

    print(f'Epoch [{epoch+1}/{num_epochs}], Loss: {total_loss/len(dataloader)}')

Epoch [1/100]:   0%|          | 0/109 [00:00<?, ?batch/s]

Epoch [1/100]:   0%|          | 0/109 [00:00<?, ?batch/s]


NameError: name 'labels' is not defined

In [622]:
play_tensors

{'2022090800_1': {'context_tensor': tensor([[ 0.,  0., 10.,  ...,  0.,  0.,  0.],
          [ 0.,  0., 10.,  ...,  0.,  0.,  0.],
          [ 0.,  0., 10.,  ...,  0.,  0.,  0.],
          ...,
          [ 0.,  0., 10.,  ...,  0.,  0.,  0.],
          [ 0.,  0., 10.,  ...,  0.,  0.,  0.],
          [ 0.,  0., 10.,  ...,  0.,  0.,  0.]]),
  'player_tensor': tensor([[[ 0.0000e+00,  1.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
             0.0000e+00,  0.0000e+00],
           [ 0.0000e+00,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
             0.0000e+00,  0.0000e+00],
           [ 0.0000e+00,  0.0000e+00,  0.0000e+00,  ...,  1.0000e+00,
             0.0000e+00,  0.0000e+00],
           ...,
           [ 1.0000e-02,  0.0000e+00,  1.0000e-02,  ...,  8.9710e+01,
             6.0120e+01,  8.2210e+01],
           [ 6.3550e+01,  2.4711e+02,  2.8787e+02,  ...,  2.9960e+01,
             1.9112e+02,  3.3640e+01],
           [ 2.6556e+02,  1.8437e+02,  2.6588e+02,  ..., -1.2140e+01,
            -

In [ ]:
model.eval()
with torch.no_grad():
    for batch in test_dataloader:
        play_data = batch['play_data']
        context_data = batch['context_data']
        lengths = batch['lengths']
        output = model(play_data, context_data, lengths)
        # Compute evaluation metrics

# Inference
new_play_data = ...  # Your new play data
new_context_data = ...  # Your new context data
new_lengths = ...  # Your new sequence lengths
model.eval()
with torch.no_grad():
    prediction = model(new_play_data, new_context_data, new_lengths)

In [576]:
label_table

shape: (212_214, 4)
┌────────────────┬─────────┬─────────────┬──────────────────┐
│ Id             ┆ frameId ┆ pff_manZone ┆ pff_passCoverage │
│ ---            ┆ ---     ┆ ---         ┆ ---              │
│ str            ┆ i64     ┆ str         ┆ str              │
╞════════════════╪═════════╪═════════════╪══════════════════╡
│ 2022090800_1   ┆ 76      ┆ Zone        ┆ Cover-6          │
│ 2022090800_1   ┆ 77      ┆ Zone        ┆ Cover-6          │
│ 2022090800_1   ┆ 78      ┆ Zone        ┆ Cover-6          │
│ 2022090800_1   ┆ 79      ┆ Zone        ┆ Cover-6          │
│ 2022090800_1   ┆ 80      ┆ Zone        ┆ Cover-6          │
│ …              ┆ …       ┆ …           ┆ …                │
│ 2022091901_111 ┆ 75      ┆ Other       ┆ Red Zone         │
│ 2022091901_111 ┆ 76      ┆ Other       ┆ Red Zone         │
│ 2022091901_111 ┆ 77      ┆ Other       ┆ Red Zone         │
│ 2022091901_111 ┆ 78      ┆ Other       ┆ Red Zone         │
│ 2022091901_111 ┆ 79      ┆ Other       ┆ Red Zone         │
└────────────────┴─────────┴─────────────┴──────────────────┘

In [591]:
label_table.filter(pl.col("Id") == play_id)["pff_manZone"].first()


'Zone'

In [578]:
from torch.utils.data import Dataset, DataLoader
from torch.nn.utils.rnn import pad_sequence


class PlayCoverageDataset(Dataset):
    def __init__(self, play_tensors, label_table):
        self.play_tensors = play_tensors
        self.label_map = {"Zone": 1, "Man": 0} 
        
        # Create dictionary of play_id -> label
        self.labels = {}
        for play_id in play_tensors.keys():
            label = label_table.filter(pl.col("Id") == play_id)["pff_manZone"].first()
            self.labels[play_id] = self.label_map[label]
        self.play_ids = list(play_tensors.keys())
    
    def __len__(self):
        return len(self.play_ids)
    
    def __getitem__(self, idx):
        play_id = self.play_ids[idx]
        tensors = self.play_tensors[play_id]
        label = self.labels[play_id]
        return {
            'context': tensors['context_tensor'],
            'players': tensors['player_tensor'],
            'label': torch.tensor(label, dtype=torch.float),
            'seq_length': tensors['context_tensor'].shape[0]
        }

def collate_fn(batch):
    lengths = torch.tensor([item['seq_length'] for item in batch])
    
    # Pad sequences to longest in batch
    context_tensors = pad_sequence([item['context'] for item in batch], batch_first=True)
    player_tensors = pad_sequence([item['players'] for item in batch], batch_first=True)
    labels = torch.stack([item['label'] for item in batch])
    
    return {
        'context': context_tensors,
        'players': player_tensors,
        'labels': labels,
        'lengths': lengths
    }

def create_dataloaders(play_tensors, label_table, batch_size=32, train_split=0.7, val_split=0.15):
    dataset = PlayCoverageDataset(play_tensors, label_table)
    
    total_size = len(dataset)
    train_size = int(train_split * total_size)
    val_size = int(val_split * total_size)
    test_size = total_size - train_size - val_size
    
    train_dataset, val_dataset, test_dataset = torch.utils.data.random_split(
        dataset, 
        [train_size, val_size, test_size]
    )
    
    train_loader = DataLoader(
        train_dataset,
        batch_size=batch_size,
        shuffle=True,
        collate_fn=collate_fn
    )
    
    val_loader = DataLoader(
        val_dataset,
        batch_size=batch_size,
        shuffle=False,
        collate_fn=collate_fn
    )
    
    test_loader = DataLoader(
        test_dataset,
        batch_size=batch_size,
        shuffle=False,
        collate_fn=collate_fn
    )
    
    return train_loader, val_loader, test_loader



In [594]:
# 1. Create your dataset first
dataset = PlayCoverageDataset(play_tensors, label_table)

# 2. Create splits and dataloaders
train_loader, val_loader, test_loader = create_dataloaders(play_tensors, label_table)

# 3. Save EVERYTHING including the dataset
torch.save({
    'play_tensors': play_tensors,
    'labels': label_table,
    'dataset': dataset,  # Save the dataset
    'train_indices': train_loader.dataset.indices,
    'val_indices': val_loader.dataset.indices,
    'test_indices': test_loader.dataset.indices
}, 'manZone_data.pt')

In [582]:

# Create splits first
train_loader, val_loader, test_loader = create_dataloaders(play_tensors, label_table)

torch.save({
    'play_tensors': play_tensors,
    'labels': label_table,
    'train_indices': train_loader.dataset.indices,  # Save the split indices
    'val_indices': val_loader.dataset.indices,
    'test_indices': test_loader.dataset.indices
}, 'manZone_data.pt')

In [580]:
label_table

shape: (212_214, 4)
┌────────────────┬─────────┬─────────────┬──────────────────┐
│ Id             ┆ frameId ┆ pff_manZone ┆ pff_passCoverage │
│ ---            ┆ ---     ┆ ---         ┆ ---              │
│ str            ┆ i64     ┆ str         ┆ str              │
╞════════════════╪═════════╪═════════════╪══════════════════╡
│ 2022090800_1   ┆ 76      ┆ Zone        ┆ Cover-6          │
│ 2022090800_1   ┆ 77      ┆ Zone        ┆ Cover-6          │
│ 2022090800_1   ┆ 78      ┆ Zone        ┆ Cover-6          │
│ 2022090800_1   ┆ 79      ┆ Zone        ┆ Cover-6          │
│ 2022090800_1   ┆ 80      ┆ Zone        ┆ Cover-6          │
│ …              ┆ …       ┆ …           ┆ …                │
│ 2022091901_111 ┆ 75      ┆ Other       ┆ Red Zone         │
│ 2022091901_111 ┆ 76      ┆ Other       ┆ Red Zone         │
│ 2022091901_111 ┆ 77      ┆ Other       ┆ Red Zone         │
│ 2022091901_111 ┆ 78      ┆ Other       ┆ Red Zone         │
│ 2022091901_111 ┆ 79      ┆ Other       ┆ Red Zone         │
└────────────────┴─────────┴─────────────┴──────────────────┘

In [41]:
from sklearn.preprocessing import LabelEncoder

y = (
    play_table
    .group_by("Id")
    .agg(pl.col("pff_manZone").first())
    .to_numpy()[:, 1]  # Get just the coverage values, exclude Id column
)
label_encoder = LabelEncoder()
y = label_encoder.fit_transform(y)